# Features showcase <a target="_blank" href="https://colab.research.google.com/github/yWorks/yfiles-jupyter-graphs-for-kuzu/blob/kuzu/examples/features.ipynb"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

This notebook shows some features of `yfiles-jupyter-graphs-for-kuzu`.

## Install required dependencies

In [ ]:
%pip install kuzu --quiet
%pip install yfiles_jupyter_graphs_for_kuzu --quiet

You can also open this notebook in Google Colab when Google Colab's custom widget manager is enabled:

In [ ]:
try:
  import google.colab
  from google.colab import output
  output.enable_custom_widget_manager()
except:
  pass

## Download sample data

For demonstration purpose, download some sample data from [kuzudb.com](https://kuzudb.com) and create a local database with it.

In [ ]:
import requests

urls = [
    "https://kuzudb.com/data/movie-lens/movies.csv",
    "https://kuzudb.com/data/movie-lens/users.csv",
    "https://kuzudb.com/data/movie-lens/ratings.csv",
    "https://kuzudb.com/data/movie-lens/tags.csv"
]

for url in urls:
    filename = url.split("/")[-1]
    response = requests.get(url)
    with open(filename, 'wb') as f:
        f.write(response.content)
    print(f"Downloaded {filename}")

## Create sample database

Use the dowloaded CSV files to create a sample database.

In [ ]:
import shutil
import kuzu

db_path = './_db_ml-small'
shutil.rmtree(db_path, ignore_errors=True)

def load_data(connection):
    connection.execute('CREATE NODE TABLE Movie (movieId INT64, year INT64, title STRING, genres STRING, PRIMARY KEY (movieId))')
    connection.execute('CREATE NODE TABLE User (userId INT64, PRIMARY KEY (userId))')
    connection.execute('CREATE REL TABLE Rating (FROM User TO Movie, rating DOUBLE, timestamp INT64)')
    connection.execute('CREATE REL TABLE Tags (FROM User TO Movie, tag STRING, timestamp INT64)')

    connection.execute('COPY Movie FROM "./movies.csv" (HEADER=TRUE)')
    connection.execute('COPY User FROM "./users.csv" (HEADER=TRUE)')
    connection.execute('COPY Rating FROM "./ratings.csv" (HEADER=TRUE)')
    connection.execute('COPY Tags FROM "./tags.csv" (HEADER=TRUE)')

db = kuzu.Database(db_path)
conn = kuzu.Connection(db)
load_data(conn)

# Default, no-config visualization

Easily visualize the result of a query.

In [ ]:
from yfiles_jupyter_graphs_for_kuzu import KuzuGraphWidget
g = KuzuGraphWidget(conn)
g.show_cypher('MATCH (u:User)-[r:Rating]->(m:Movie) RETURN u, r, m LIMIT 250')

# Data-driven visualization

The visualization of nodes and relationships can be adjusted through data-mappings (see [README](https://github.com/yWorks/yfiles-jupyter-graphs-for-kuzu/blob/kuzu/README.md) for details).

In [ ]:
from yfiles_jupyter_graphs_for_kuzu import KuzuGraphWidget
g = KuzuGraphWidget(conn)

g.add_node_configuration('Movie', 
     text = lambda node : {
        'text': 'Title:\n' + node['properties']['title'],
        'backgroundColor': 'rgba(0,0,0,0.7)', 
        'fontSize': 20, 
        'color': '#FFFFFF', 
        'position': 'south', 
        'fontWeight': 'lighter',
        'maximumWidth': 300, 
        'wrapping': 'word', 
        'textAlignment': 'center'
    },
    styles = {'shape': 'pill'},
    size = (150, 60))

g.add_relationship_configuration('Rating', color = 'grey', text = lambda rel : {'text': 'Rating: ' + str(rel['properties']['rating'])})

g.show_cypher('MATCH (u:User)-[r:Rating]->(m:Movie) RETURN u, r, m LIMIT 250')

# Automatic layouts

The widget offers several automatic layouts like `hierarchic`, `organic`, `interactive_organic`, `circular`, `radial`, `orthogonal`, and `tree`. Each layout serves a different purpose and can help highlight different aspects of the diagram.

You can either choose the layout interactively through the UI of the widget, or programmatically when defining it. For example, set the `circular` layout like so:

In [ ]:
from yfiles_jupyter_graphs_for_kuzu import KuzuGraphWidget
g = KuzuGraphWidget(conn)
g.show_cypher('MATCH (u:User)-[r:Rating]->(m:Movie) RETURN u, r, m LIMIT 250', layout='circular')

# Heatmap

The heat map overlay is another useful way to show an additional layer of information. It maps numerical data to a heatmap which can be used to easily find hotspots in the dataset.

In this case, we show the `rating` property of the dataset as heatmap overlay.

In [ ]:
from yfiles_jupyter_graphs_for_kuzu import KuzuGraphWidget
g = KuzuGraphWidget(conn)

def heat_mapping(element):
    max_rating = 5
    min_rating = 0
    if "rating" in element["properties"]:
        rating = element["properties"]["rating"]
        # result needs to be within (0,1)
        normalized_value = (rating - min_rating) / (max_rating - min_rating)
        return max(0, min(1, normalized_value))

g.add_node_configuration("Rating", heat=heat_mapping)

g.show_cypher('MATCH (u:User)-[r:Rating]->(m:Movie) RETURN u, r, m LIMIT 250')

# Grouping

There are different ways to group nodes. Either use already given node objects in the dataset or generate new "artifical" nodes that are used as groups.

In this case, we group the nodes by type and create new "artifical" group nodes that are not part of the initial input data. The new data objects are also considered for any data-driven visualization mappings. So you could also style them separately.

In [ ]:
from yfiles_jupyter_graphs_for_kuzu import KuzuGraphWidget
g = KuzuGraphWidget(conn)

g.add_node_configuration('Movie', parent_configuration='movies')
g.add_node_configuration('User', parent_configuration='users')

g.show_cypher('MATCH (u:User)-[r:Rating]->(m:Movie) RETURN u, r, m LIMIT 50', layout='hierarchic')